# Machine learning 

In this part, we use machine learning (ML) models, particularly random forests (RF), to predict the cytotoxicity of our previously processed dataset. As a reminder the dataset contains morphological compounds for around 30k molecules as well as their smiles computer morgan fingerprint.

## Import libraries and previous data


In [1]:

import copy

import pandas as pd
import numpy as np
from rdkit import Chem
from rdkit.Chem.MolStandardize import rdMolStandardize
from sklearn.model_selection import train_test_split, cross_validate
from sklearn.ensemble import RandomForestRegressor
from sklearn.dummy import DummyRegressor
from sklearn.metrics import mean_squared_error


### Load data : per-treatment profile fingerprints and annotation file

- Load cytotoxicity files :  _INVITRODBv3_20181017.xls_ and _ cytotox_invitrodb_v4_1_SEPT2023.xlsx_ from the [ToxCast database](https://www.epa.gov/chemical-research/toxicity-forecaster-toxcasttm-data).
- Load fingerprint file named _fingerprint_ds.pkl_ generated in _Part2-Similarity_Analysis.ipynb_ 
- Concatenate the data frames into one 

1. Load the data 

In [2]:
dataset = pd.read_pickle('../Data/Output/fingerprint_ds.pkl')
dataset.head()

Metadata_broad_sample       CPD_NAME  \
0  BRD-K08693008-001-01-9  BRD-K08693008   
1  BRD-K63982890-001-01-9  BRD-K63982890   
2  BRD-K41006887-001-01-9  BRD-K41006887   
3  BRD-K06226868-001-01-9  BRD-K06226868   
4  BRD-K80296876-001-01-1  BRD-K80296876   

                                          CPD_SMILES  Cells_AreaShape_Area  \
0  OC[C@@H]1O[C@@H](CCn2cc(nn2)C2CCCCC2)CC[C@@H]1...              0.048556   
1  OC[C@@H]1O[C@@H](CCn2cc(nn2)C2CCCCC2)CC[C@H]1N...             -0.452493   
2  OC[C@H]1O[C@@H](CCn2cc(nn2)C2CCCCC2)CC[C@@H]1N...             -0.057586   
3  OC[C@H]1O[C@@H](CCn2cc(nn2)C2CCCCC2)CC[C@H]1NC...             -0.479600   
4  OC[C@@H]1O[C@H](CCn2cc(nn2)C2CCCCC2)CC[C@@H]1N...             -0.640931   

   Cells_AreaShape_Center_X  Cells_AreaShape_Center_Y  \
0                  1.511688                  0.671310   
1                  0.951788                  0.099538   
2                  1.049698                  0.849837   
3                 -0.420351                  0.579931   
4                 -0.311103                  0.639001   

   Cells_AreaShape_Compactness  Cells_AreaShape_Extent  \
0                     1.608372               -1.506759   
1                     0.742492               -0.919170   
2                     1.010880               -0.987492   
3                    -0.186314               -0.499758   
4                    -0.391112                0.278096   

   Cells_AreaShape_FormFactor  Cells_AreaShape_MajorAxisLength  ...  \
0                   -0.511226                         0.287326  ...   
1                   -0.953408                        -0.217596  ...   
2                    0.477225                         0.282021  ...   
3                    0.066921                        -0.409035  ...   
4                   -0.171686                        -0.729866  ...   

   Nuclei_Texture_Variance_AGP_10_0  Nuclei_Texture_Variance_ER_10_0  \
0                          1.585885                         0.789273   
1                          0.335412                         0.184112   
2                          0.571320                        -0.010077   
3                          0.430315                         0.036771   
4                          1.547239                        -0.022274   

   Nuclei_Texture_Variance_Mito_10_0  Nuclei_Texture_Variance_RNA_10_0  \
0                          -0.522186                         -1.089521   
1                          -1.211516                         -1.750300   
2                          -0.679660                         -0.620206   
3                          -1.474867                          0.611439   
4                           0.386308                          0.864965   

                                           STD_smile  \
0  OC[C@@H]1O[C@@H](CCn2cc(C3CCCCC3)nn2)CC[C@@H]1...   
1  OC[C@@H]1O[C@@H](CCn2cc(C3CCCCC3)nn2)CC[C@H]1N...   
2  OC[C@H]1O[C@@H](CCn2cc(C3CCCCC3)nn2)CC[C@@H]1N...   
3  OC[C@H]1O[C@@H](CCn2cc(C3CCCCC3)nn2)CC[C@H]1NC...   
4  OC[C@@H]1O[C@H](CCn2cc(C3CCCCC3)nn2)CC[C@@H]1N...   

                                         morganB_fps  \
0  [0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
1  [0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
2  [0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
3  [0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
4  [0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   

   euclidean_distance_morganB_fps  tanimoto_distance_morganB_fps  \
0                        9.539392                       0.163229   
1                        9.539392                       0.163229   
2                        9.539392                       0.163229   
3                        9.539392                       0.163229   
4                        9.539392                       0.163229   

                           morphological_fingerprint  \
0  [0.04855643906188584, 1.5116882801514897, 0.67...   
1  [-0.4524933924732235, 0.9517883246940788, 0.09...   
2  [-0.057586365661270

In this part we won't neet drop the euclidean distances per fingerprint so this colunms can be droped.


In [3]:
dataset.drop(['euclidean_distance_morganB_fps', 'euclidean_distance_morphological_fingerprint'], axis = 1, inplace=True)

2. Load annotation file 

In [4]:
cpd_summary = pd.read_excel('../Data/Annotations/INVITRODBv3_20181017.xls')
cpd_summary.head(3)

DTXSID                  PREFERRED_NAME       CASRN  \
0  DTXSID0020020  4-Acetylaminophenylacetic acid  18699-02-0   
1  DTXSID0020022                     Acifluorfen  50594-66-6   
2  DTXSID0020024          Acrolein diethylacetal   3054-95-3   

                      INCHIKEY  \
0  MROJXXOCABQVEF-UHFFFAOYSA-N   
1  NUFNQYOELLVIPL-UHFFFAOYSA-N   
2  MCIPQLOKVXSHTD-UHFFFAOYSA-N   

                                          IUPAC_NAME  \
0                     (4-Acetamidophenyl)acetic acid   
1  5-[2-Chloro-4-(trifluoromethyl)phenoxy]-2-nitr...   
2                             3,3-Diethoxyprop-1-ene   

                                              SMILES  \
0                        CC(=O)NC1=CC=C(CC(O)=O)C=C1   
1  OC(=O)C1=C(C=CC(OC2=CC=C(C=C2Cl)C(F)(F)F)=C1)[...   
2                                       CCOC(OCC)C=C   

                                        INCHI_STRING MOLECULAR_FORMULA  \
0  InChI=1S/C10H11NO3/c1-7(12)11-9-4-2-8(3-5-9)6-...         C10H11NO3   
1  InChI=1S/C14H7ClF3NO5/c15-10-5-7(14(16,17)18)1...      C14H7ClF3NO5   
2  InChI=1S/C7H14O2/c1-4-7(8-5-2)9-6-3/h4,7H,1,5-...           C7H14O2   

  AVERAGE_MASS MONOISOTOPIC_MASS  DATA_SOURCES NUMBER_OF_PUBMED_ARTICLES  \
0      193.202        193.073893            35                        19   
1       361.66        360.996485            66                        50   
2      130.187         130.09938            28                         1   

  PUBCHEM_DATA_SOURCES CPDAT_COUNT  
0                   92           2  
1                   74          36  
2                   73           2

It should be noted that the `cpd_summary` dataset contains various chemical identifiers. The first seven rows are chemical identifiers, the next three rows represent molecular properties, and the last four rows contain metadata.

In [5]:
cytotox_labels = pd.read_excel('../Data/Annotations/cytotox_invitrodb_v4_1_SEPT2023.xlsx')
cytotox_labels.head(3)


chid      casn           chnm dsstox_substance_id  cytotox_median_raw  \
0  20005   60-35-5      Acetamide       DTXSID7020005                 NaN   
1  20007  968-81-0  Acetohexamide       DTXSID7020007                 NaN   
2  20009   75-05-8   Acetonitrile       DTXSID7020009                 NaN   

   cytotox_mad  global_mad  cytotox_median_log  cytotox_median_um  \
0          NaN    0.159707                 3.0             1000.0   
1          NaN    0.159707                 3.0             1000.0   
2          NaN    0.159707                 3.0             1000.0   

   cytotox_lower_bound_um  ntested  nhit  cytotox_lower_bound_log  \
0                  1000.0       71     0                      3.0   
1                  1000.0       67     0                      3.0   
2                  1000.0       67     0                      3.0   

         created_date  
0 2023-05-02 19:03:09  
1 2023-05-02 19:03:09  
2 2023-05-02 19:03:09

Similarly,`cytotox_labels` contains chemical identifiers, cell toxicity-related data, and a column of metadata.

In [6]:
print(f'The cell toxiciy dataset contains data on {len(cytotox_labels.casn.unique())} unique molecules')

The cell toxiciy dataset contains data on 9090 unique molecules


With one glance, one note that both dataframe has missing value. In the previous Jupiter notebook, we showed you how to handle missing values. <br>
As mentioned above, there are only $9,090$ molecules in Toxcast against $30,000$ in our initial data, therefore while combining both we will obtain at most 9090 molecules annotated with cell toxicity or less. 


## Merging the different files into one dataset 

Here we want to merge our files; morphological - structural fingerprint, data about cytotoxicity  to obtain a unique  dataset containing all molecules informations. 

1. Pre-processing SMILES from toxcast dataset files

Similarly as in `Part2-Similarirty_Analysis.ipynb` the compounds' SMILE from the ToxCast dataset need to be standardized. <br>
To this end, we use a similar function as in `Part2-Similarirty_Analysis.ipynb > Molecular Fingerprint > 1. Pre-processing the smiles`. <br>
However, we needed to add steps, where NaN values were dropped since the SMILES were not available for all compounds.

In [7]:
def clean_std_smiles(dataset):
    
    '''
    Clean, uncharge parents' smiles, get Inchi to standardize smiles
        Parameters : 
            dataset (data frame): data frame having a column named 'SMILES' with smiles
        Returns : 
            dataset (data frame): same data frame with one more column named 'STD_smile'
    '''
    
    dataset['Molecule'] = dataset.apply(lambda x: Chem.MolFromSmiles(x['SMILES']), axis = 1)
    dataset.dropna(subset=['Molecule'], inplace=True)
    clean_mol = [rdMolStandardize.Cleanup(mol) for mol in dataset['Molecule'].values ]
    parent_clean_mol = [rdMolStandardize.FragmentParent(mol) for mol in clean_mol]
    #uncharger = rdMolStandardize.Uncharger() 
    #uncharged_parent_clean_mol = [uncharger.uncharge(mol)for mol in parent_clean_mol]
    

    try : inchi = [Chem.MolToInchi(mol) for mol in parent_clean_mol]
    except : print(f'cannot convert this smile into Inchi' )
    
    std_smile = list(map(Chem.MolFromInchi,inchi))
    dataset['STD_SMILE_MOLECULE'] = std_smile
    dataset.dropna(subset=['STD_SMILE_MOLECULE'], inplace=True)
    dataset['STD_SMILES'] = dataset.apply(lambda x: Chem.MolToSmiles(x['STD_SMILE_MOLECULE']), axis=1)
    # drop unnecessary columns
    dataset.drop(['STD_SMILE_MOLECULE', 'Molecule'], axis=1, inplace=True)
    return dataset

In [8]:
cpd_summary = clean_std_smiles(cpd_summary)
cpd_summary = cpd_summary.loc[:, ['DTXSID', 'SMILES', 'STD_SMILES']]

[14:18:02] SMILES Parse Error: syntax error while parsing: -
[14:18:02] SMILES Parse Error: Failed parsing SMILES '-' for input: '-'
[14:18:02] SMILES Parse Error: syntax error while parsing: -
[14:18:02] SMILES Parse Error: Failed parsing SMILES '-' for input: '-'
[14:18:02] SMILES Parse Error: syntax error while parsing: -
[14:18:02] SMILES Parse Error: Failed parsing SMILES '-' for input: '-'
[14:18:02] SMILES Parse Error: syntax error while parsing: -
[14:18:02] SMILES Parse Error: Failed parsing SMILES '-' for input: '-'
[14:18:02] SMILES Parse Error: syntax error while parsing: -
[14:18:02] SMILES Parse Error: Failed parsing SMILES '-' for input: '-'
[14:18:02] SMILES Parse Error: syntax error while parsing: -
[14:18:02] SMILES Parse Error: Failed parsing SMILES '-' for input: '-'
[14:18:02] SMILES Parse Error: syntax error while parsing: -
[14:18:02] SMILES Parse Error: Failed parsing SMILES '-' for input: '-'
[14:18:02] SMILES Parse Error: syntax error while parsing: -
[14:18:0

2. Join tox-cast datasets with morphological dataset 

To join the ToxCast Compound IDs to the dataset containing the fingerprints, we additionally, need the compound information of the ToxCast compounds. 
Which includes the SMILE representation of the compounds contains in `cpd_summary`.

In [9]:
label_with_smiles = cpd_summary.join(cytotox_labels.set_index('dsstox_substance_id'), on='DTXSID')
label_with_smiles.dropna(subset=['STD_SMILES', 'cytotox_median_log'])
label_with_smiles = label_with_smiles.loc[:, ['STD_SMILES', 'cytotox_median_log']]

And join the cytotoxicity data with our morphological compound fingerprints on the standardized SMILES.

In [10]:
full_dataset = dataset.join(label_with_smiles.set_index('STD_SMILES'), on='STD_smile')

3. We drop all columns without response.

In [11]:
full_dataset.dropna(subset=['cytotox_median_log'], inplace=True)
full_dataset.drop(['Metadata_broad_sample', 'STD_smile', 'CPD_SMILES'], axis = 1, inplace = True)
full_dataset.reset_index(inplace=True)
full_dataset.head(2)

index                                           CPD_NAME  \
0  12105  (?)-Epinephrine hydrochloride[(?)-Adrenalin hy...   
1  12429                                         mibefradil   

   Cells_AreaShape_Area  Cells_AreaShape_Center_X  Cells_AreaShape_Center_Y  \
0              0.051314                  0.022129                 -0.865925   
1             -1.460491                 -0.223908                 -0.078846   

   Cells_AreaShape_Compactness  Cells_AreaShape_Extent  \
0                     0.986814               -0.926390   
1                     0.915392               -0.164692   

   Cells_AreaShape_FormFactor  Cells_AreaShape_MajorAxisLength  \
0                   -0.392892                         0.301329   
1                    2.010525                        -1.159373   

   Cells_AreaShape_MaximumRadius  ...  Nuclei_Texture_SumVariance_AGP_10_0  \
0                      -0.351116  ...                            -0.988105   
1                      -1.651189  ...                            -1.022865   

   Nuclei_Texture_SumVariance_ER_10_0  Nuclei_Texture_Variance_AGP_10_0  \
0                           -0.399111                         -0.729723   
1                           -0.254321                         -0.770142   

   Nuclei_Texture_Variance_ER_10_0  Nuclei_Texture_Variance_Mito_10_0  \
0                        -0.419997                          -0.610496   
1                        -0.409785                          -0.650856   

   Nuclei_Texture_Variance_RNA_10_0  \
0                         -0.793366   
1                         -0.947376   

                                         morganB_fps  \
0  [0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
1  [0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   

   tanimoto_distance_morganB_fps  \
0                       0.110701   
1                       0.158273   

                           morphological_fingerprint  cytotox_median_log  
0  [0.05131359908370006, 0.022128734128407407, -0...            3.000000  
1  [-1.4604913347931925, -0.22390788657837601, -0...            1.292396  

[2 rows x 585 columns]

In [12]:
print(f'Now, we have left {len(full_dataset)} compounds with associated cytotoxicity value.')

Now, we have left 902 compounds with associated cytotoxicity value.


## Spliting Data in Training and TestSet

For ML, we always need training and a test set that are pairwise disjoint. <br>
To this end, we split the data into two parts, where the training set will contain 80% of the samples and the test set the remaining 20%. <br>
Moreover, we need a response vector y, i.e., the column with the cytotoxicity information and a feature matrix X, i.e., a matrix with the morphological or molecular fingerprints or a combination thereof, for each compound.

1. Features and variable to predict (response vector)

In [13]:
y = copy.deepcopy(full_dataset['cytotox_median_log'].values)
X = full_dataset.copy(deep=True)
X.drop(['index','morganB_fps','morphological_fingerprint'],axis=1,inplace=True)
#X.drop(['cytotox_median_log', 'CPD_NAME', 'morphological_fingerprint', 'morganB_fps', 'STD_smile', 'CPD_SMILES'], axis = 1, inplace = True)

In [14]:
X_train, X_test, y_train, y_test = train_test_split(X.iloc[:,1:], y, test_size=0.2, random_state=42, shuffle=True)

## Cross Validation and Hyperparameter Tuning

In ML, we want to minimize a loss function, e.g., the mean-squared error (MSE). In particular, we want to fit the training data in order to minimize the loss on the training samples, while still having a small error on the unseen test samples. Moreover, there are hyperparameters defining the hypothesis space of the model, which can be tuned in order to minimize the estimated test error. The test error can be estimated using a so-called k-fold cross validation (CV), which is performed in the following.

For an RF, there are three hyperparameters that we want to tune in order to optimize the estimated test error: 
* depth of the trees in the forest: 10, 20, or 30
* number of trees in the forest: 100, 300, or 500
* minimum number of samples per leaf: 10, 15, or 20

In [15]:
def rf_cross_validation(X_train, y_train, max_depth_range = [10,20,30], num_tree_range = [100,300,500], min_samples_leaf_range = [10,15,20]):
    '''
        performs a 5-fold CV for a Random Forest for given X_train and y_train
        
        @param X_train: the training matrix
        @param y_train: the associated response vector
        @param max_depth_range: list containing the values that should be tested for max depth, default [10,20,30]
        @param num_tree_range: list containing the values that should be tested for the number of trees, default [100,300,500]
        @param min_samples_leaf_range: list containing the values that should be tested for the minimum number of samples per leaf, default [10,15,20]
        
        @return: a forest with the best hyperparameter according to the estimated test MSE and trained on the whole training set
    '''
    best_score = -float('inf')
    for depth in max_depth_range:
        cv_results = cross_validate(RandomForestRegressor(random_state=42, max_depth=depth,n_jobs=-1), X = X_train, y=y_train, scoring='neg_mean_squared_error', verbose=4, cv=5)
        score = np.mean(cv_results['test_score'])
        if score > best_score:
            best_score = score
            best_depth = depth
            
    best_score = -float('inf')
    for n_tree in num_tree_range:
        cv_results = cross_validate(RandomForestRegressor(random_state=42, n_estimators=n_tree,n_jobs=-1), X = X_train, y=y_train, scoring='neg_mean_squared_error', verbose=4, cv=5)
        score = np.mean(cv_results['test_score'])
        if score > best_score:
            best_score = score
            best_n_tree = n_tree
    
    best_score = -float('inf')
    for num_samples in min_samples_leaf_range:
        cv_results = cross_validate(RandomForestRegressor(random_state=42, min_samples_leaf=num_samples,n_jobs=-1), X = X_train, y=y_train, scoring='neg_mean_squared_error', verbose=4, cv=5)
        score = np.mean(cv_results['test_score'])
        if score > best_score:
            best_score = score
            best_min_samples = num_samples
    
    rf = RandomForestRegressor(random_state=42, n_estimators=best_n_tree, max_depth=best_depth, min_samples_leaf=best_min_samples,n_jobs=-1)
    rf.fit(X_train, y_train)
    return rf

Will need, approximately X minutes (1.33 min Floriane , 90 LM)as the training process per split is quite time consuming.

In [16]:
best_estimator = rf_cross_validation(X_train, y_train)

[CV] END ......................................, score=-0.000 total time=   0.7s
[CV] END ......................................, score=-0.002 total time=   0.6s
[CV] END ......................................, score=-0.000 total time=   0.7s
[CV] END ......................................, score=-0.005 total time=   0.8s
[CV] END ......................................, score=-0.009 total time=   0.6s
[CV] END ......................................, score=-0.000 total time=   0.7s
[CV] END ......................................, score=-0.002 total time=   0.7s
[CV] END ......................................, score=-0.000 total time=   0.6s
[CV] END ......................................, score=-0.005 total time=   0.8s
[CV] END ......................................, score=-0.009 total time=   0.7s
[CV] END ......................................, score=-0.000 total time=   0.6s
[CV] END ......................................, score=-0.002 total time=   0.7s
[CV] END ...................

Now, we print the hyperparameters of the forest, to see what performed best in the CV.

In [17]:
param_dict = best_estimator.get_params()
print(f'We use a max depth of {param_dict["max_depth"]}, {param_dict["n_estimators"]} trees, and at least {param_dict["min_samples_leaf"]} samples per leaf.')

We use a max depth of 20, 100 trees, and at least 10 samples per leaf.


## Prediction on Test Set 

Now, we predict for the test data, i.e., so far unseen samples to assess the real test error.

In [18]:
random_forest = best_estimator
y_pred  = random_forest.predict(X_test)

And assess the MSE on our test set prediciton.

In [19]:
print(f'The RF trained on morphological fingerprints reached an MSE of {mean_squared_error(y_pred=y_pred, y_true=y_test)}')

The RF trained on morphological fingerprints reached an MSE of 0.0008381547899697418


## Using Molecular (Morgan) Fingerprints

1. Features and variable to predict (response vector)

In [20]:
y = copy.deepcopy(full_dataset['cytotox_median_log'].values)
X = full_dataset.copy(deep=True)
X = X.loc[:, ['morganB_fps']].values

In [21]:
new_X = []
for i, l in enumerate(X):
    new_X.append(np.array(l[0]))
X_morgan = np.array(new_X)

In [22]:
X_train, X_test, y_train, y_test = train_test_split(X_morgan, y, test_size=0.2, random_state=42, shuffle=True)

In [23]:
rf_morgan = RandomForestRegressor(random_state=42)

In [24]:
rf_morgan.fit(X_train, y_train)

RandomForestRegressor(random_state=42)

In [25]:
y_pred_rf_morgan = rf_morgan.predict(X_test)

In [26]:
mean_squared_error(y_true=y_test, y_pred=y_pred_rf_morgan)

0.47137702364283196

## Using both Molecular (Morgan) and Morphological Fingerprints

In [27]:
X = full_dataset.copy(deep=True)
X = X.loc[:, ['morphological_fingerprint', 'morganB_fps']]
X['appended_profile'] = X.apply(lambda x: np.concatenate([x['morphological_fingerprint'], x['morganB_fps']]), axis=1)
X.drop(['morphological_fingerprint', 'morganB_fps'], axis=1, inplace=True)

In [28]:
X = X.values

In [30]:
new_X = []
for i, l in enumerate(X):
    new_X.append(np.array(l[0]))
new_X = np.array(new_X)

In [31]:
X_train, X_test, y_train, y_test = train_test_split(new_X, y, test_size=0.2, random_state=42, shuffle=True)

In [32]:
rf_combined_morgan_morph  = RandomForestRegressor(random_state=42)

In [33]:
rf_combined_morgan_morph.fit(X_train, y_train)

RandomForestRegressor(random_state=42)

In [34]:
y_pred_combi = rf_combined_morgan_morph.predict(X_test)

In [35]:
mean_squared_error(y_true=y_test, y_pred=y_pred_combi)

0.39725960181496855

To do LM (biologist proof):
- DMSO as control (know that it is not toxic)+ 1 molecule known to be toxic chemoterapeutics 
- a concret exemple with 2 molecules 